In [5]:
import torch
import torch.nn as nn
import numpy as np
import cv2
import pickle
from tqdm import tqdm
import random
import os
import glob
from topologylayer.nn import AlphaLayer, BarcodePolyFeature, PartialSumBarcodeLengths, RipsLayer, TopKBarcodeLengths
import kmapper as km
import sklearn
import matplotlib.pyplot as plt

In [6]:
dir_name = '/home/administrator/Sidhanth/topo_fe/pickled_data/'

def pickle_data(name,data,dir_name=dir_name):
    pickle_file = dir_name + name
    pickle_in = open(pickle_file,'wb')
    pickle.dump(data,pickle_in)
    pickle_in.close()
    
def pickle_load(pickle_file):
    pickle_out = open(pickle_file,'rb')
    data = pickle.load(pickle_out)
    pickle_out.close()
    return data
    
def load_pickle_file(name,img_size,dataset_path=None,dir_name=dir_name):
    path_string = '_' + str(img_size) + '.pickle'
    pickle_file = dir_name + name + path_string
    
    if os.path.exists(pickle_file):
        data = pickle_load(pickle_file)
        return data
    
    elif dataset_path is not None:
        def load_data(dataset_path=dataset_path):
            data = []
            index = 0
            for data_class in dataset_path:
                data_paths = sorted(glob.glob(data_class))
                class_num = dataset_path.index(data_class)
                print(class_num)
                count = 0
                for data_path in tqdm(data_paths):
                    try:
                        img = cv2.imread(data_path,1)
                        img = cv2.resize(img,(img_size,img_size),interpolation=cv2.INTER_CUBIC)
                        data.append([np.asarray(img),class_num])
                        count += 1
                    except Exception as e:
                        print(path+':Corrupt file')
                        pass
                print('Class '+str(class_num)+':'+str(count))
                index += 1
            return data
        
        dataset = load_data()
        random.shuffle(dataset)
        x = []
        y = []
        
        for images,labels in dataset:
            x.append(images)
            y.append(labels)
            
        x,y = np.array(x),np.array(y)
        print(x.shape,y.shape)
        pickle_data('x' + path_string,x)
        pickle_data('y' + path_string,y)
        data = pickle_load(pickle_file)
        return data

In [8]:
html_path = '/home/administrator/Sidhanth/topo_fe/mapper_outputs/'
path = '/home/administrator/Sidhanth/Datasets/cat_dog_dataset/training_set/'
cat_dataset_path = path + 'cats/cat.*.jpg'
dog_dataset_path = path + 'dogs/dog.*.jpg'
dataset_path = [cat_dataset_path,dog_dataset_path]

img_size = 32
batch_size = 4

x = load_pickle_file('x',img_size,dataset_path=dataset_path)
y = load_pickle_file('y',img_size)

print(x.shape,y.shape)

(8000, 32, 32, 3) (8000,)


In [9]:
def g_filter(x=img_size,y=img_size,thetas=[np.pi*x/4. for x in range(8)]):
    img_filter = np.empty([len(thetas),x,y])
    for k,theta in tqdm(enumerate(thetas)):    
        for i in range(x):
            for j in range(y):
                img_filter[k][i][j] = (i+1)*np.cos(theta) + (j+1)*np.sin(theta)
    return img_filter

conv_filter = g_filter()
pickle_data('filters',conv_filter)

8it [00:00, 212.91it/s]


In [16]:
from sklearn.preprocessing import normalize

def feature_engineering(images,persistence_dims=[0,1],ps=5,qs=5):
    features = []
    for i0 in persistence_dims:
        for p in range(ps):
            for q in range(qs):
                features += [BarcodePolyFeature(i0,p,q)]
    
    batch_size = images.shape[0]
    layer = RipsLayer(batch_size)
    
    final_feat = []
    
    images = np.reshape(images,newshape=(batch_size,-1))
    images = normalize(images)
    for image in images:
        image = torch.from_numpy(image).float()
        temp_feat = []
        for feature in features:
            temp_feat.append(feature(layer(image)).cuda())
        
        temp_feat = torch.stack(temp_feat).float()
        final_feat.append(temp_feat)
        del temp_feat
        
    final_feat = torch.flatten(torch.stack(final_feat).float())
    final_feat = final_feat.cpu().numpy()
    #print(final_feat.shape)
    return final_feat

In [17]:
images = x
filters = pickle_load(dir_name + 'filters')

print(images.shape,filters.shape)
features = []

for image in tqdm(images):
    image_set = []
    for filter in filters:
        image_set.append(np.multiply(np.moveaxis(image,-1,0),filter))
    
    image_set = np.array(image_set)
    features.append(feature_engineering(image_set))
    del image_set
    
pickle_data('features',features)


  0%|          | 0/8000 [00:00<?, ?it/s]

(8000, 32, 32, 3) (8, 32, 32)



  2%|▏         | 148/8000 [01:12<1:09:15,  1.89it/s]


  4%|▎         | 294/8000 [02:26<1:04:54,  1.98it/s]


  6%|▌         | 440/8000 [03:38<1:03:40,  1.98it/s]


...

 94%|█████████▍| 7544/8000 [1:01:21<03:47,  2.01it/s]


 96%|█████████▌| 7687/8000 [1:02:30<02:30,  2.08it/s]


 98%|█████████▊| 7830/8000 [1:03:38<01:21,  2.07it/s]


100%|█████████▉| 7973/8000 [1:04:47<00:13,  2.06it/s]


100%|██████████| 8000/8000 [1:05:00<00:00,  2.07it/s]

In [18]:
features = np.array(features)
features.shape,y.shape

rob_scaler = sklearn.preprocessing.RobustScaler()
features = rob_scaler.fit_transform(features)

In [19]:
x_train,x_test,y_train,y_test = sklearn.model_selection.train_test_split(features,y,test_size=0.2)
classifier = sklearn.linear_model.LogisticRegression(solver='newton-cg',verbose=1,n_jobs=-1).fit(x_train,y_train)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 out of   1 | elapsed:    2.2s finished


In [20]:
y_val = classifier.predict(x_test)
print(sklearn.metrics.accuracy_score(y_test,y_val))

0.556875


In [21]:
mapper = km.KeplerMapper(verbose=2)
projected_data = mapper.fit_transform(features,projection=sklearn.manifold.TSNE())

KeplerMapper()
..Composing projection pipeline of length 1:
	Projections: TSNE(angle=0.5, early_exaggeration=12.0, init='random', learning_rate=200.0,
     method='barnes_hut', metric='euclidean', min_grad_norm=1e-07,
     n_components=2, n_iter=1000, n_iter_without_progress=300, perplexity=30.0,
     random_state=None, verbose=0)
	Distance matrices: False
	Scalers: MinMaxScaler(copy=True, feature_range=(0, 1))
..Projecting on data shaped (8000, 400)

..Projecting data using: 
	TSNE(angle=0.5, early_exaggeration=12.0, init='random', learning_rate=200.0,
     method='barnes_hut', metric='euclidean', min_grad_norm=1e-07,
     n_components=2, n_iter=1000, n_iter_without_progress=300, perplexity=30.0,
     random_state=None, verbose=2)

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 8000 samples in 0.109s...
[t-SNE] Computed neighbors for 8000 samples in 7.781s...
[t-SNE] Computed conditional probabilities for sample 1000 / 8000
[t-SNE] Computed conditional probabilities for sam

In [23]:
graph = mapper.map(projected_data,
                  clusterer=sklearn.cluster.DBSCAN(eps=100,min_samples=5,metric='haversine'),
                  cover=km.Cover(60,0.45))
mapper.visualize(graph,title='Cat-Dog Mapper',path_html=html_path+'map.html',color_function=y,custom_tooltips=y)

Mapping on data shaped (8000, 2) using lens shaped (8000, 2)

Minimal points in hypercube before clustering: 5
Creating 3600 hypercubes.
   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

Cube_15 is empty.

Cube_16 is empty.

   > Found 1 clusters.

Cube_18 is empty.

Cube_19 is empty.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

Cube_36 is empty.



   > Found 1 clusters.

Cube_544 is empty.

   > Found 1 clusters.

   > Found 1 clusters.

Cube_547 is empty.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

Cube_575 is empty.

   > Found 1 clusters.

   > Found 1 clusters.

Cube_578 is empty.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Fou

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

Cube_1092 is empty.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

Cube_1098 is empty.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

   > Found 1 clusters.

Cube_1121 is empty.

   > Found 1 clusters.

   > Found 1 clusters.

 


Created 4150 edges and 1353 nodes in 0:00:02.517086.
Wrote visualization to: /home/administrator/Sidhanth/topo_fe/mapper_outputs/map.html


'<!DOCTYPE html>\n<html>\n\n<head>\n  <meta charset="utf-8">\n  <meta name="generator" content="KeplerMapper">\n  <title>Cat-Dog Mapper | KeplerMapper</title>\n\n  <link rel="icon" type="image/png" href="http://i.imgur.com/axOG6GJ.jpg" />\n\n  <link href=\'https://fonts.googleapis.com/css?family=Roboto+Mono:700,300\' rel=\'stylesheet\' type=\'text/css\'>\n  <style>* {\n  margin: 0;\n  padding: 0;\n}\n\nhtml, body {\n  height: 100%;\n}\n\nbody {\n  font-family: "Roboto Mono", "Helvetica", sans-serif;\n  font-size: 14px;\n}\n\n#logo {\n  position: absolute;\n  right: 00px;\n  top: 0px;\n  width: 90px;\n  height: 90px;\n  z-index: 999999;\n}\n\n#display {\n  color: #95A5A6;\n  background: #212121;\n}\n\n#print {\n  color: #000;\n  background: #FFF;\n}\n\nh1 {\n  font-size: 21px;\n  font-weight: 300;\n  font-weight: 300;\n}\n\nh2 {\n  font-size: 18px;\n  padding-bottom: 20px;\n  font-weight: 300;\n}\n\nh3 {\n  font-size: 14px;\n  font-weight: 700;\n  text-transform: uppercase;\n}\n\nh4 {\n